In [55]:
import pandas as pd
pd.set_option('display.max_rows', None)
from bs4 import BeautifulSoup
import bs4 as bs4
from urllib.parse import urlparse
import requests
from collections import Counter
import pandas as pd
import os

In [56]:
category_df=pd.read_csv("spam.csv",encoding='ISO-8859-1')
df=pd.read_csv("spam.csv",encoding='ISO-8859-1')

url=[]
for i in category_df['message']:
    url.append(i)

In [57]:
class ScraperTool:
    def visit_url(self, website_url):
        '''
        Visit URL. Download the Content. Initialize the beautifulsoup object. Call parsing methods. Return Series object.
        '''
        headers = {'User-Agent': 'Mozilla/5.0 (Windows NT 6.3; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/54.0.2840.71 Safari/537.36'}
        content = requests.get(website_url,headers=headers,timeout=20).content
        
        #lxml is apparently faster than other settings.
        soup = BeautifulSoup(content, "lxml")
        result = {
#             "website_url": website_url,
            "message": self.get_message(message)
#             "title_tag_content": self.get_html_title_tag(soup),
#             "meta_tag_content": self.get_html_meta_tags(soup),
#             "headings_content": self.get_html_heading_tags(soup),
#             "html_text_content": self.get_text_content(soup)
        }
        #get_tag_count returns a dynamic dictionary. That is why we update the dictionary with a separate update command.
        result.update(self.get_tag_count(soup))
        
        #Convert to Series object and return
        return pd.Series(result)
    
    def get_message(self,message):
        return message
    

In [58]:
import spacy as sp
from collections import Counter
sp.prefer_gpu()
import en_core_web_sm
#anconda prompt ko run as adminstrator and copy paste this:python -m spacy download en
nlp = en_core_web_sm.load()
import re
def clean_text(doc):
    '''
    Clean the document. Remove pronouns, stopwords, lemmatize the words and lowercase them
    '''
    doc = nlp(doc)
    tokens = []
    exclusion_list = ["nan"]
    for token in doc:
        if token.is_stop or token.is_punct or token.text.isnumeric() or (token.text.isalnum()==False) or token.text in exclusion_list :
            continue
        token = str(token.lemma_.lower().strip())
        tokens.append(token)
    return " ".join(tokens) 

In [59]:
finance=["stock","market","business","finance","financial","economical","analysis","research",
          "jobs","investing","investor","market","marketing","valuation","mortgage","mutual",
          "funds","estate","data","portfolio","entrepreneurship","strategy", "marketing", "company", "employee",
           "startup","payment","work","advertising","build","buy","sell","insurance","salary","consumer","share", "money",
          "investor","buying","management","wealth","legal","opportunity","successful","stipend","expensive",
          "economic","currencies","billion","crisis","unemployment","hospitality","industry","trading",'company',
          "professional", "cheap", "retirement","association","accountants","tax","accounting","accountant","professional",
         "accountancy","finance","manager","corporate","financial","accountability","management","resource","cgfm",'supply',
         "agent","taxation","business",'store','merchantile','services','service','client','consulting','corporation','markets',
         'products','production','export','gift','industrial','consultation','consult','office','exporter','range','cultivator',
         'investment','industries','ship','commerce','credit','aircraft','maitainance','aviation','purchase','shop','distributor',
          'equipment','import','sale','rentals','rental','investors','commercial','retail','workspace','consultation','product',
         'organisation','organization','productivity','freelance','freelancer','serve',"digital","banking","bank","loan",
          "credit","debit",'customer','merchandise','inventory','wholesale','manufacturing','manufacturer',
         "money","saving","savings","economic","investment","home","deposit","corporation","bankunderground","commercial",
          "investing","branch","payment","transaction","overdraft","loans","insurance","investor","industries","industry","company",
         "fund","alliance","stock","invest","price","dividend","broker","department","document","project","mining","mineral",
         "asset","construction","capital","oil","gas","regulations","infrastructure","investors","solar","nextenergy","market",
         "markets","trade","office",'member']
adultery=["porn","pornography","sex","masturbation","bdsm","erotic",'blonde','milf','Hardcore','tits','tit','boobs','pussy','ass',
       'creampie','busty','skinny','fantasy','fantasies','brunette','interracial','hentai','dick','threesome','gangbang','anal',
       'lesbian','gay','masturbate','bondage','doggystyle','nipples','oral','amateur','naked','hookup','cumshot','hairy',
       'fetish','handjobs','webcam','erotica','bisexual','hardcore','milfs','cock',"hd","video","pornhub","free","videos",
      "premium","amateur","fuck","xxx","creampie","cum","teen","milf","pornstar","brazzers","pussy","views","sexy","tits",
      "gay","fucking","bhabhi","black","horny","straight","blonde","blowjob","brunette","rank","anal","porno","bbc","ass",
      "tit","boob","suck","slut","animation","hentai","girl","indian","desi","lesbian","threesome","mom","wife","gangbang",
      "hardcore","dirty","transgender","rough","woman","busty","vporn","massage","hard","single","lonely"]
keywords=finance + adultery

In [60]:
from flashtext.keyword import KeywordProcessor
kp0=KeywordProcessor()
for word in keywords:
    kp0.add_keyword(word)
kp1=KeywordProcessor()
for word in finance:
    kp1.add_keyword(word)
kp2=KeywordProcessor()
for word in adultery:
    kp2.add_keyword(word)

In [61]:
def percentage1(dum0,dumx):
    try:
        ans=float(dumx)/float(dum0)
        ans=ans*100
    except:
        return 0
    else:
        return ans
def check_title(x):
#     title=df['website_name'].loc[df['cleaned_website_text']==x]
#     title=list(title)[0]
#     test_list=['forum'] 
#     res = [ele for ele in test_list if(ele in title)]
    return x
def check_url(x):
#     url=df['website_url'].loc[df['cleaned_website_text']==x]
#     url=list(url)[0]
#     test_list=['.edu','.ac.'] 
#     res = ["Education" for ele in test_list if(ele in url)]
    return x

In [62]:
def find_totalkeywords(x):
    Total_matches=kp0.extract_keywords(x)
    y0=len(Total_matches)
    return y0
def find_category(x):
    global m1,m2,m3,m4,m5
    global Category1,Category2,Category3,Category4,Category5
    y0=find_totalkeywords(x)
    y_1=kp1.extract_keywords(x)
    y1 = len(y_1)
    y_2=kp2.extract_keywords(x)
    y2 = len(y_2)
    per1 = float(percentage1(y0,y1))
    per2 = float(percentage1(y0,y2))
    check_forum=check_title(x)
    if check_forum:
        per7=100.00
    check_edu=check_url(x)
    if check_edu:
        per11=100.0
    if y0==0:
        Category1='None'
        Category2='None'
        m1=0.0
        m2=0.0
        matched_catkeywords='None'
    else:
        per={per1:"Finance",per2:"Adultery"}
        all_keys=per.keys()
        m1=max(all_keys)
        Category1=per[m1]
        del per[m1]
        if per:
            all_keys=per.keys()
            m2=max(all_keys)
            Category2=per[m2]
            del per[m2]
        else:
            m2=0.0
            Category2='None'
        keywords={"Finance":y_1,"Adultery":y_2}
        matched_catkeywords=keywords[Category1]
    return y0,matched_catkeywords,Category1,m1,Category2,m2

In [63]:
# dff = df[df["class"] == "spam"]

# dff.head()

In [64]:
Total=[]
match=[]
Cat1=[]
percent1=[]
Cat2=[]
percent2=[]
final={}
for i in df['message']:
    Total.append(find_category(i)[0])
    match.append(find_category(i)[1])
    Cat1.append(find_category(i)[2])
    percent1.append(find_category(i)[3])
    Cat2.append(find_category(i)[4])
    percent2.append(find_category(i)[5])
    
# df['message']=Total
df['matched_category_keywords']=match
df['Category1']=Cat1
df['percent1']=percent1
df['Category2']=Cat2
df['percent2']=percent2
new=pd.DataFrame(final)
df=df.join(new)
df

class                                            message  \
0      ham  Go until jurong point, crazy.. Available only ...   
1      ham                      Ok lar... Joking wif u oni...   
2     spam  Free entry in 2 a wkly comp to win FA Cup fina...   
3      ham  U dun say so early hor... U c already then say...   
4      ham  Nah I don't think he goes to usf, he lives aro...   
5     spam  FreeMsg Hey there darling it's been 3 week's n...   
6      ham  Even my brother is not like to speak with me. ...   
7      ham  As per your request 'Melle Melle (Oru Minnamin...   
8     spam  WINNER!! As a valued network customer you have...   
9     spam  Had your mobile 11 months or more? U R entitle...   
10     ham  I'm gonna be home soon and i don't want to tal...   
11    spam  SIX chances to win CASH! From 100 to 20,000 po...   
12    spam  URGENT! You have won a 1 week FREE membership ...   
13     ham  I've been searching for the right words to tha...   
14     ham                I HAVE A DATE ON SUNDAY WITH WILL!!   
15    spam  XXXMobileMovieClub: To use your credit, click ...   
16     ham                         Oh k...i'm watching here:)   
17     ham  Eh u remember how 2 spell his name... Yes i di...   
18     ham  Fine if thatåÕs the way u feel. ThatåÕs the wa...   
19    spam  England v Macedonia - dont miss the goals/team...   
20     ham          Is that seriously how you spell his name?   
21     ham  IÛ÷m going to try for 2 months ha ha only joking   
22     ham  So Ì_ pay first lar... Then when is da stock c...   
23     ham  Aft i finish my lunch then i go str down lor. ...   
24     ham  Ffffffffff. Alright no way I can meet up with ...   
25     ham  Just forced myself to eat a slice. I'm really ...   
26     ham                     Lol your always so convincing.   
27     ham  Did you catch the bus ? Are you frying an egg ...   
28     ham  I'm back &amp; we're packing the car now, I'll...   
29     ham  Ahhh. Work. I vaguely remember that! What does...   
30     ham  Wait that's still not all that clear, were you...   
31     ham  Yeah he got in at 2 and was v apologetic. n ha...   
32     ham                      K tell me anything about you.   
33     ham  For fear of fainting with the of all that hous...   
34    spam  Thanks for your subscription to Ringtone UK yo...   
35     ham  Yup... Ok i go home look at the timings then i...   
36     ham    Oops, I'll let you know when my roommate's done   
37     ham                       I see the letter B on my car   
38     ham                        Anything lor... U decide...   
39     ham  Hello! How's you and how did saturday go? I wa...   
40     ham  Pls go ahead with watts. I just wanted to be s...   
41     ham  Did I forget to tell you ? I want you , I need...   
42    spam  07732584351 - Rodger Burns - MSG = We tried to...   
43     ham                                WHO ARE YOU SEEING?   
44     ham  Great! I hope you like your man well endowed. ...   
45     ham                   No calls..messages..missed calls   
46     ham      Didn't you get hep b immunisation in nigeria.   
47     ham                    Fair enough, anything going on?   
48     ham  Yeah hopefully, if tyler can't do it I could m...   
49     ham  U don't know how stubborn I am. I didn't even ...   
50     ham  What you thinked about me. First time you saw ...   
51     ham  A gram usually runs like  &lt;#&gt; , a half e...   
52     ham  K fyi x has a ride early tomorrow morning but ...   
53     ham  Wow. I never realized that you were so embaras...   
54    spam  SMS. ac Sptv: The New Jersey Devils and the De...   
55     ham  Do you know what Mallika Sherawat did yesterda...   
56    spam  Congrats! 1 year special cinema pass for 2 is ...   
57     ham                 Sorry, I'll call later in meeting.   
58     ham                             Tell where you reached   
59     ham           Yes..gauti and sehwag out of odi series.   
60     ham  Your gonna have to pick up a

In [65]:
dff = df[df["class"] == "spam"]

dff.head()

class                                            message Unnamed: 2  \
2   spam  Free entry in 2 a wkly comp to win FA Cup fina...        NaN   
5   spam  FreeMsg Hey there darling it's been 3 week's n...        NaN   
8   spam  WINNER!! As a valued network customer you have...        NaN   
9   spam  Had your mobile 11 months or more? U R entitle...        NaN   
11  spam  SIX chances to win CASH! From 100 to 20,000 po...        NaN   

   Unnamed: 3 Unnamed: 4 matched_category_keywords Category1  percent1  \
2         NaN        NaN                    [free]  Adultery     100.0   
5         NaN        NaN                     [xxx]  Adultery     100.0   
8         NaN        NaN                [customer]   Finance     100.0   
9         NaN        NaN              [free, free]  Adultery     100.0   
11        NaN        NaN                      None      None       0.0   

   Category2  percent2  
2    Finance       0.0  
5    Finance       0.0  
8   Adultery       0.0  
9    Finance       0.0  
11      None       0.0

In [70]:
dffinal = dff[["class", "message","Category1"]]
dffinal.replace("None", "Miscellaneous", inplace=True)

<ipython-input-70-700cabb447cf>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dffinal.replace("None", "Miscellaneous", inplace=True)


In [72]:
dffinal

class                                            message      Category1
2     spam  Free entry in 2 a wkly comp to win FA Cup fina...       Adultery
5     spam  FreeMsg Hey there darling it's been 3 week's n...       Adultery
8     spam  WINNER!! As a valued network customer you have...        Finance
9     spam  Had your mobile 11 months or more? U R entitle...       Adultery
11    spam  SIX chances to win CASH! From 100 to 20,000 po...  Miscellaneous
12    spam  URGENT! You have won a 1 week FREE membership ...       Adultery
15    spam  XXXMobileMovieClub: To use your credit, click ...        Finance
19    spam  England v Macedonia - dont miss the goals/team...  Miscellaneous
34    spam  Thanks for your subscription to Ringtone UK yo...  Miscellaneous
42    spam  07732584351 - Rodger Burns - MSG = We tried to...       Adultery
54    spam  SMS. ac Sptv: The New Jersey Devils and the De...  Miscellaneous
56    spam  Congrats! 1 year special cinema pass for 2 is ...       Adultery
65    spam  As a valued customer, I am pleased to advise y...        Finance
67    spam  Urgent UR awarded a complimentary trip to Euro...  Miscellaneous
68    spam  Did you hear about the new \Divorce Barbie\"? ...  Miscellaneous
93    spam  Please call our customer service representativ...        Finance
95    spam  Your free ringtone is waiting to be collected....       Adultery
113   spam  GENT! We are trying to contact you. Last weeke...  Miscellaneous
116   spam  You are a winner U have been specially selecte...  Miscellaneous
119   spam  PRIVATE! Your 2004 Account Statement for 07742...  Miscellaneous
120   spam  URGENT! Your Mobile No. was awarded å£2000 Bon...  Miscellaneous
122   spam  Todays Voda numbers ending 7548 are selected t...  Miscellaneous
133   spam  Sunshine Quiz Wkly Q! Win a top Sony DVD playe...  Miscellaneous
134   spam  Want 2 get laid tonight? Want real Dogging loc...  Miscellaneous
138   spam  You'll not rcv any more msgs from the chat svc...       Adultery
146   spam  FreeMsg Why haven't you replied to my text? I'...       Adultery
158   spam  Customer service annoncement. You have a New Y...        Finance
159   spam  You are a winner U have been specially selecte...  Miscellaneous
163   spam  -PLS STOP bootydelious (32/F) is inviting you ...  Miscellaneous
164   spam  BangBabes Ur order is on the way. U SHOULD rec...        Finance
166   spam  URGENT! We are trying to contact you. Last wee...  Miscellaneous
187   spam  Please call our customer service representativ...        Finance
190   spam  Are you unique enough? Find out from 30th Augu...  Miscellaneous
224   spam  500 New Mobiles from 2004, MUST GO! Txt: NOKIA...  Miscellaneous
226   spam  Will u meet ur dream partner soon? Is ur caree...       Adultery
234   spam  Text & meet someone sexy today. U can find a d...       Adultery
239   spam  U 447801259231 have a secret admirer who is lo...  Miscellaneous
249   spam  Congratulations ur awarded 500 of CD vouchers ...       Adultery
258   spam  We tried to contact you re your reply to our o...       Adultery
263   spam  Hey I am really horny want to chat or see me n...       Adultery
267   spam  Ur ringtone service has changed! 25 Free credi...       Adultery
269   spam  Ringtone Club: Get the UK singles chart on you...       Adultery
272   spam  HMV BONUS SPECIAL 500 pounds of genuine HMV vo...  Miscellaneous
295   spam  T-Mobile customer you may now claim your FREE ...       Adultery
304   spam  SMS. ac Blind Date 4U!: Rodds1 is 21/m from Ab...  Miscellaneous
308   spam  TheMob> Check out our newest selection of cont...  Miscellaneous
311   spam  Think ur smart ? Win å£200 this week in our we...  Miscellaneous
318   spam  December only! Had your mobile 11mths+? You ar...       Adultery
332   spam  Call Germany for only 1 pence per minute! Call...  Miscellaneous
334   spam  Valentines Day Special! Win over å£1000 in our...  Miscellaneous
348   spam  Fancy a shag? I do.Interested? sextextuk.com t...  Miscellaneous
3

In [73]:
dffinal.to_csv("FINAL_DATASET.csv")